In [0]:
print("Hello Databricks! I’m ready to master ETL 🚀")
spark.version

Hello Databricks! I’m ready to master ETL 🚀


'4.0.0'

In [0]:
from pyspark.sql import SparkSession
spark  = SparkSession.builder.getOrCreate()

In [0]:
data = [("Alice",34), ("Bob",45),("AKshay",23), ("Neha",31)]
columns = ["Name", "Age"]
df = spark.createDataFrame(data,columns)

In [0]:
type(df)

pyspark.sql.connect.dataframe.DataFrame

In [0]:
trychange_rdd = df.rdd

---------------------------------------------------------------------------
PySparkNotImplementedError                Traceback (most recent call last)
File <command-5479999614248213>, line 1
----> 1 trychange_rdd = df.rdd

File /databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/dataframe.py:2330, in DataFrame.rdd(self)
   2328 @property
   2329 def rdd(self) -> "RDD[Row]":
-> 2330     raise PySparkNotImplementedError(
   2331         errorClass="NOT_IMPLEMENTED",
   2332         messageParameters={"feature": "rdd"},
   2333     )

PySparkNotImplementedError: [NOT_IMPLEMENTED] Using custom code using PySpark RDDs is not allowed on serverless compute. We suggest using mapInPandas or mapInArrow for the most common use cases. For more details on compatibility and limitations, check: https://docs.databricks.com/release-notes/serverless.html#limitations

In [0]:
df.show()

+------+---+
|  Name|Age|
+------+---+
| Alice| 34|
|   Bob| 45|
|AKshay| 23|
|  Neha| 31|
+------+---+



In [0]:
df = df.withColumnsRenamed({"Name":"FullName","Age":"Real_age"})
df.show()

+--------+--------+
|FullName|Real_age|
+--------+--------+
|   Alice|      34|
|     Bob|      45|
|  AKshay|      23|
|    Neha|      31|
+--------+--------+



In [0]:
df_filtered = df.filter(df.Age > 30)

In [0]:
df_filtered.explain()

== Physical Plan ==
LocalTableScan [Name#13205, Age#13206L]


== Photon Explanation ==
Photon does not fully support the query because:
		Unsupported node: LocalTableScan [Name#13205, Age#13206L].

Reference node:
	LocalTableScan [Name#13205, Age#13206L]



In [0]:
df_filtered.show()

+-----+---+
| Name|Age|
+-----+---+
|Alice| 34|
|  Bob| 45|
| Neha| 31|
+-----+---+



In [0]:
df = spark.read.format("csv")\
    .option("heeader","False")\
        .option("inferSchema","true")\
            .load("/databricks-datasets/adult/adult.data")

In [0]:
df.printSchema()
df.show(5)

root
 |-- _c0: integer (nullable = true)
 |-- _c1: string (nullable = true)
 |-- _c2: double (nullable = true)
 |-- _c3: string (nullable = true)
 |-- _c4: double (nullable = true)
 |-- _c5: string (nullable = true)
 |-- _c6: string (nullable = true)
 |-- _c7: string (nullable = true)
 |-- _c8: string (nullable = true)
 |-- _c9: string (nullable = true)
 |-- _c10: double (nullable = true)
 |-- _c11: double (nullable = true)
 |-- _c12: double (nullable = true)
 |-- _c13: string (nullable = true)
 |-- _c14: string (nullable = true)

+---+-----------------+--------+----------+----+-------------------+------------------+--------------+------+-------+------+----+----+--------------+------+
|_c0|              _c1|     _c2|       _c3| _c4|                _c5|               _c6|           _c7|   _c8|    _c9|  _c10|_c11|_c12|          _c13|  _c14|
+---+-----------------+--------+----------+----+-------------------+------------------+--------------+------+-------+------+----+----+--------------+

In [0]:
df.write.mode("overwrite").parquet("dbfs:/Volumes/learningvolume/learningschema/learningvolume/adult_parquet")

In [0]:
display(spark.sql("SHOW VOLUMES"))

database volume_name default youtubeseries_learning_v001

In [0]:
df_parquet = spark.read.parquet("dbfs:/Volumes/learningvolume/learningschema/learningvolume/adult_parquet")
df_parquet.count()

32561

In [0]:
type(df_parquet)

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-5479999614248217>, line 1
----> 1 type(df_parquet)

NameError: name 'df_parquet' is not defined

In [0]:
df.write.format("delta").mode("overwrite").saveAsTable("adult_delta")

In [0]:
%sql
select * from adult_delta
limit 5

_c0 _c1 _c2 _c3 _c4 _c5 _c6 _c7 _c8 _c9 _c10 _c11 _c12 _c13 _c14 39 State-gov 77516.0 Bachelors 13.0 Never-married Adm-clerical Not-in-family White Male 2174.0 0.0 40.0 United-States <=50K 50 Self-emp-not-inc 83311.0 Bachelors 13.0 Married-civ-spouse Exec-managerial Husband White Male 0.0 0.0 13.0 United-States <=50K 38 Private 215646.0 HS-grad 9.0 Divorced Handlers-cleaners Not-in-family White Male 0.0 0.0 40.0 United-States <=50K 53 Private 234721.0 11th 7.0 Married-civ-spouse Handlers-cleaners Husband Black Male 0.0 0.0 40.0 United-States <=50K 28 Private 338409.0 Bachelors 13.0 Married-civ-spouse Prof-specialty Wife Black Female 0.0 0.0 40.0 Cuba <=50K

In [0]:
%sql
SELECT occupation, COUNT(*) AS cnt FROM adult_delta GROUP BY occupation ORDER BY cnt DESC LIMIT 10



---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-6567446825871463>, line 1
----> 1 get_ipython().run_cell_magic('sql', '', 'SELECT occupation, COUNT(*) AS cnt FROM adult_delta GROUP BY occupation ORDER BY cnt DESC LIMIT 10\n')

File /databricks/python/lib/python3.12/site-packages/IPython/core/interactiveshell.py:2541, in InteractiveShell.run_cell_magic(self, magic_name, line, cell)
   2539 with self.builtin_trap:
   2540     args = (magic_arg_s, cell)
-> 2541     result = fn(*args, **kwargs)
   2543 # The code below prevents the output from being displayed
   2544 # when using magics with decorator @output_can_be_silenced
   2545 # when the last Python token in the expression is a ';'.
   2546 if getattr(fn, magic.MAGIC_OUTPUT_CAN_BE_SILENCED, False):

File /databricks/python_shell/lib/dbruntime/sql_magic/sql_magic.py:194, in SqlMagic.sql(self, line, cell)
    188 except

In [0]:
df = spark.table("adult_delta")


In [0]:
print(type(df))
df.printSchema()

<class 'pyspark.sql.connect.dataframe.DataFrame'>
root
 |-- _c0: integer (nullable = true)
 |-- _c1: string (nullable = true)
 |-- _c2: double (nullable = true)
 |-- _c3: string (nullable = true)
 |-- _c4: double (nullable = true)
 |-- _c5: string (nullable = true)
 |-- _c6: string (nullable = true)
 |-- _c7: string (nullable = true)
 |-- _c8: string (nullable = true)
 |-- _c9: string (nullable = true)
 |-- _c10: double (nullable = true)
 |-- _c11: double (nullable = true)
 |-- _c12: double (nullable = true)
 |-- _c13: string (nullable = true)
 |-- _c14: string (nullable = true)



In [0]:
rddfile = df.rdd

---------------------------------------------------------------------------
PySparkNotImplementedError                Traceback (most recent call last)
File <command-7589350825677592>, line 1
----> 1 rddfile = df.rdd

File /databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/dataframe.py:2330, in DataFrame.rdd(self)
   2328 @property
   2329 def rdd(self) -> "RDD[Row]":
-> 2330     raise PySparkNotImplementedError(
   2331         errorClass="NOT_IMPLEMENTED",
   2332         messageParameters={"feature": "rdd"},
   2333     )

PySparkNotImplementedError: [NOT_IMPLEMENTED] Using custom code using PySpark RDDs is not allowed on serverless compute. We suggest using mapInPandas or mapInArrow for the most common use cases. For more details on compatibility and limitations, check: https://docs.databricks.com/release-notes/serverless.html#limitations

In [0]:
def process(pdf):
    # Custom logic here
    return pdf

result_df = df.mapInPandas(
    process,
    schema=df.schema
)

display(result_df)

_c0 _c1 _c2 _c3 _c4 _c5 _c6 _c7 _c8 _c9 _c10 _c11 _c12 _c13 _c14 39 State-gov 77516.0 Bachelors 13.0 Never-married Adm-clerical Not-in-family White Male 2174.0 0.0 40.0 United-States <=50K 50 Self-emp-not-inc 83311.0 Bachelors 13.0 Married-civ-spouse Exec-managerial Husband White Male 0.0 0.0 13.0 United-States <=50K 38 Private 215646.0 HS-grad 9.0 Divorced Handlers-cleaners Not-in-family White Male 0.0 0.0 40.0 United-States <=50K 53 Private 234721.0 11th 7.0 Married-civ-spouse Handlers-cleaners Husband Black Male 0.0 0.0 40.0 United-States <=50K 28 Private 338409.0 Bachelors 13.0 Married-civ-spouse Prof-specialty Wife Black Female 0.0 0.0 40.0 Cuba <=50K 37 Private 284582.0 Masters 14.0 Married-civ-spouse Exec-managerial Wife White Female 0.0 0.0 40.0 United-States <=50K 49 Private 160187.0 9th 5.0 Married-spouse-absent Other-service Not-in-family Black Female 0.0 0.0 16.0 Jamaica <=50K 52 Self-emp-not-inc 209642.0 HS-grad 9.0 Married-civ-spouse Exec-managerial Husband White Male 0.0 0.0 45.0 United-States >50K 31 Private 45781.0 Masters 14.0 Never-married Prof-specialty Not-in-family White Female 14084.0 0.0 50.0 United-States >50K 42 Private 159449.0 Bachelors 13.0 Married-civ-spouse Exec-managerial Husband White Male 5178.0 0.0 40.0 United-States >50K 37 Private 280464.0 Some-college 10.0 Married-civ-spouse Exec-managerial Husband Black Male 0.0 0.0 80.0 United-States >50K 30 State-gov 141297.0 Bachelors 13.0 Married-civ-spouse Prof-specialty Husband Asian-Pac-Islander Male 0.0 0.0 40.0 India >50K 23 Private 122272.0 Bachelors 13.0 Never-married Adm-clerical Own-child White Female 0.0 0.0 30.0 United-States <=50K 32 Private 205019.0 Assoc-acdm 12.0 Never-married Sales Not-in-family Black Male 0.0 0.0 50.0 United-States <=50K 40 Private 121772.0 Assoc-voc 11.0 Married-civ-spouse Craft-repair Husband Asian-Pac-Islander Male 0.0 0.0 40.0 ? >50K 34 Private 245487.0 7th-8th 4.0 Married-civ-spouse Transport-moving Husband Amer-Indian-Eskimo Male 0.0 0.0 45.0 Mexico <=50K 25 Self-emp-not-inc 176756.0 HS-grad 9.0 Never-married Farming-fishing Own-child White Male 0.0 0.0 35.0 United-States <=50K 32 Private 186824.0 HS-grad 9.0 Never-married Machine-op-inspct Unmarried White Male 0.0 0.0 40.0 United-States <=50K 38 Private 28887.0 11th 7.0 Married-civ-spouse Sales Husband White Male 0.0 0.0 50.0 United-States <=50K 43 Self-emp-not-inc 292175.0 Masters 14.0 Divorced Exec-managerial Unmarried White Female 0.0 0.0 45.0 United-States >50K 40 Private 193524.0 Doctorate 16.0 Married-civ-spouse Prof-specialty Husband White Male 0.0 0.0 60.0 United-States >50K 54 Private 302146.0 HS-grad 9.0 Separated Other-service Unmarried Black Female 0.0 0.0 20.0 United-States <=50K 35 Federal-gov 76845.0 9th 5.0 Married-civ-spouse Farming-fishing Husband Black Male 0.0 0.0 40.0 United-States <=50K 43 Private 117037.0 11th 7.0 Married-civ-spouse Transport-moving Husband White Male 0.0 2042.0 40.0 United-States <=50K 59 Private 109015.0 HS-grad 9.0 Divorced Tech-support Unmarried White Female 0.0 0.0 40.0 United-States <=50K 56 Local-gov 216851.0 Bachelors 13.0 Married-civ-spouse Tech-support Husband White Male 0.0 0.0 40.0 United-States >50K 19 Private 168294.0 HS-grad 9.0 Never-married Craft-repair Own-child White Male 0.0 0.0 40.0 United-States <=50K 54 ? 180211.0 Some-college 10.0 Married-civ-spouse ? Husband Asian-Pac-Islander Male 0.0 0.0 60.0 South >50K 39 Private 367260.0 HS-grad 9.0 Divorced Exec-managerial Not-in-family White Male 0.0 0.0 80.0 United-States <=50K 49 Private 193366.0 HS-grad 9.0 Married-civ-spouse Craft-repair Husband White Male 0.0 0.0 40.0 United-States <=50K 23 Local-gov 190709.0 Assoc-acdm 12.0 Never-married Protective-serv Not-in-family White Male 0.0 0.0 52.0 United-States <=50K 20 Private 266015.0 Some-college 10.0 Never-married Sales Own-child Black Male 0.0 0.0 44.0 United-States <=50K 45 Private 386940.0 Bachelors 13.0 Divorced Exec-managerial Own-child White Male 0.0 1408.0 40.0 United-States <=50K 30 Federal-gov 59

In [0]:
print(type(result_df))
result_df.take(5)

<class 'pyspark.sql.connect.dataframe.DataFrame'>


[Row(_c0=39, _c1=' State-gov', _c2=77516.0, _c3=' Bachelors', _c4=13.0, _c5=' Never-married', _c6=' Adm-clerical', _c7=' Not-in-family', _c8=' White', _c9=' Male', _c10=2174.0, _c11=0.0, _c12=40.0, _c13=' United-States', _c14=' <=50K'),
 Row(_c0=50, _c1=' Self-emp-not-inc', _c2=83311.0, _c3=' Bachelors', _c4=13.0, _c5=' Married-civ-spouse', _c6=' Exec-managerial', _c7=' Husband', _c8=' White', _c9=' Male', _c10=0.0, _c11=0.0, _c12=13.0, _c13=' United-States', _c14=' <=50K'),
 Row(_c0=38, _c1=' Private', _c2=215646.0, _c3=' HS-grad', _c4=9.0, _c5=' Divorced', _c6=' Handlers-cleaners', _c7=' Not-in-family', _c8=' White', _c9=' Male', _c10=0.0, _c11=0.0, _c12=40.0, _c13=' United-States', _c14=' <=50K'),
 Row(_c0=53, _c1=' Private', _c2=234721.0, _c3=' 11th', _c4=7.0, _c5=' Married-civ-spouse', _c6=' Handlers-cleaners', _c7=' Husband', _c8=' Black', _c9=' Male', _c10=0.0, _c11=0.0, _c12=40.0, _c13=' United-States', _c14=' <=50K'),
 Row(_c0=28, _c1=' Private', _c2=338409.0, _c3=' Bachelors'

In [0]:
df.show()

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-8341505426707782>, line 1
----> 1 df.show()

NameError: name 'df' is not defined